In [1]:
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegressionCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier, BaggingClassifier
from sklearn.metrics import f1_score, recall_score, precision_score
import pickle
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

In [2]:
df = pd.read_csv('train_LZV4RXX.csv')  # reading train data

In [3]:
df

loan_id  age  education proof_submitted  loan_amount  asset_cost  \
0           1   27        1.0          Aadhar       504264      820920   
1           2   48        1.0          Aadhar       728556      831444   
2           3   30        2.0         VoterID       642936      826092   
3           4   28        1.0          Aadhar       746556      930924   
4           5   29        1.0          Aadhar      1139880     1902000   
...       ...  ...        ...             ...          ...         ...   
6995     6996   45        2.0          Aadhar       930948     1258344   
6996     6997   41        2.0          Aadhar       681108      791040   
6997     6998   47        2.0          Aadhar       627636      720336   
6998     6999   39        1.0          Aadhar       654708      793860   
6999     7000   31        1.0          Aadhar       705108      900660   

      no_of_loans  no_of_curr_loans  last_delinq_none  loan_default  
0               2                 2                 0             0  
1               6                 2                 0             0  
2               0                 0                 0             1  
3               0                 0                 0             0  
4               0                 0                 0             0  
...           ...               ...               ...           ...  
6995            0                 0                 0             1  
6996            4                 4                 0             1  
6997           35                11                 0             1  
6998            0                 0                 0             1  
6999            0                 0                 0             0  

[7000 rows x 10 columns]

In [6]:
pf = df.profile_report()  # EDA

In [7]:
pf.to_file('EDA_report.html')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
df.corr()

loan_id       age  education  loan_amount  asset_cost  \
loan_id           1.000000 -0.017165  -0.034615    -0.020757   -0.032053   
age              -0.017165  1.000000   0.102063    -0.058011   -0.122741   
education        -0.034615  0.102063   1.000000    -0.004588    0.083221   
loan_amount      -0.020757 -0.058011  -0.004588     1.000000    0.735176   
asset_cost       -0.032053 -0.122741   0.083221     0.735176    1.000000   
no_of_loans      -0.023589  0.193026   0.025889     0.010867   -0.052643   
no_of_curr_loans -0.015454  0.184503   0.004606     0.014788   -0.054021   
last_delinq_none -0.002829  0.050325   0.026516    -0.009412   -0.023489   
loan_default      0.011921 -0.029571   0.041701     0.115736    0.048020   

                  no_of_loans  no_of_curr_loans  last_delinq_none  \
loan_id             -0.023589         -0.015454         -0.002829   
age                  0.193026          0.184503          0.050325   
education            0.025889          0.004606          0.026516   
loan_amount          0.010867          0.014788         -0.009412   
asset_cost          -0.052643         -0.054021         -0.023489   
no_of_loans          1.000000          0.774705          0.235024   
no_of_curr_loans     0.774705          1.000000          0.272716   
last_delinq_none     0.235024          0.272716          1.000000   
loan_default        -0.045738         -0.057306          0.014772   

                  loan_default  
loan_id               0.011921  
age                  -0.029571  
education             0.041701  
loan_amount           0.115736  
asset_cost            0.048020  
no_of_loans          -0.045738  
no_of_curr_loans     -0.057306  
last_delinq_none      0.014772  
loan_default          1.000000

## EDA observations <br>
- education has 245 missing values<br>
- loan amount is normally distributed curve <br>
- loan amount is highly correlated with asset_cost<br>
- no_of_loans has 3615 zero values and it is highly correlated with no_of_curr_loans<br>
- no_of_curr_loans has 4220 zero values and it is highly correlated with no_of_loans

In [9]:
df['education'] = df['education'].fillna(method='bfill') # back filling

## Training and Testing data preparation 

- first type of data only excluding loan_id and proof_submitted

In [10]:
x1 = df.drop(['loan_id','proof_submitted','loan_default'], axis = 1)
y1 = df[['loan_default']]

In [11]:
x1_train, x1_test, y1_train, y1_test = train_test_split(x1, y1, test_size=0.20, random_state=0)

- second type of data excluding loan_id, proof_submitted,education and no_of_curr_loans

In [12]:
x2 = df.drop(['loan_id','education','proof_submitted','no_of_curr_loans','loan_default'], axis = 1)
y2 = df[['loan_default']]

In [13]:
x2_train, x2_test, y2_train, y2_test = train_test_split(x2, y2, test_size=0.20, random_state=0)

# Model building

### Random forest with first dataset

In [14]:
grid_param_rf1 = {'n_estimators': [0,5,10,20,50,120],
               'criterion': ['gini','entropy'],
               'max_depth': range(1,10),
               'min_samples_leaf': range(1,10)
                }

rf1_grid = GridSearchCV(RandomForestClassifier(), param_grid= grid_param_rf1, cv=5, verbose=3)

In [15]:
rf1_grid.fit(x1_train,y1_train)

Fitting 5 folds for each of 972 candidates, totalling 4860 fits


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 349, in fit
    self._validate_estimator()
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\ensemble\_base.py", line 133, in _validate_estimator
    raise ValueError("n_estimators must be

[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 2/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 3/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 4/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 5/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 2/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector 

[CV 3/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 4/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 5/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s


...

[CV 4/5] END criterion=entropy, max_depth=9, min_samples_leaf=9, n_estimators=120; total time=   1.3s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)


[CV 5/5] END criterion=entropy, max_depth=9, min_samples_leaf=9, n_estimators=120; total time=   1.2s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [       nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59535714 0.59714286 0.59625    0.59625    0.59625
        nan 0.59589286 0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59642857 0.59607143 0.59625    0.59625    0.59625
        nan 0.59625    0

GridSearchCV(cv=5, estimator=RandomForestClassifier(),
             param_grid={'criterion': ['gini', 'entropy'],
                         'max_depth': range(1, 10),
                         'min_samples_leaf': range(1, 10),
                         'n_estimators': [0, 5, 10, 20, 50, 120]},
             verbose=3)

In [16]:
rf1_grid.best_params_

{'criterion': 'gini',
 'max_depth': 7,
 'min_samples_leaf': 9,
 'n_estimators': 120}

In [17]:
f1_score(y1_test, rf1_grid.predict(x1_test), average= 'macro')

0.45723319340089685

## Random forest with 2nd dataset

In [18]:
grid_param_rf2 = {'n_estimators': [0,5,10,20,50,120],
               'criterion': ['gini','entropy'],
               'max_depth': range(1,10),
               'min_samples_leaf': range(1,10)
                }

rf2_grid = GridSearchCV(RandomForestClassifier(), param_grid= grid_param_rf2, cv=5, verbose=3)

In [19]:
rf2_grid.fit(x2_train,y2_train)

Fitting 5 folds for each of 972 candidates, totalling 4860 fits
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 2/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 3/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 4/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 5/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=0; total time=   0.0s
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 2/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 3/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 4/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:610: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 593, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\ensemble\_forest.py", line 349, in fit
    self._validate_estimator()
  File "C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\ensemble\_base.py", line 133, in _validate_estimator
    raise ValueError("n_estimators must be

[CV 5/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=5; total time=   0.0s
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s
[CV 2/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s
[CV 3/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)


[CV 4/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s
[CV 5/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=10; total time=   0.0s
[CV 1/5] END criterion=gini, max_depth=1, min_samples_leaf=1, n_estimators=20; total time=   0.0s


...

[CV 4/5] END criterion=entropy, max_depth=9, min_samples_leaf=9, n_estimators=120; total time=   1.3s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:593: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)


[CV 5/5] END criterion=entropy, max_depth=9, min_samples_leaf=9, n_estimators=120; total time=   1.3s


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:918: UserWarning: One or more of the test scores are non-finite: [       nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59625    0.59625    0.59625    0.59625    0.59625
        nan 0.59535714 0.59642857 0.595      0.59642857 0.59625
        nan 0.59571429 0.59625    0.59660714 0.59607143 0.59625
        nan 0.59589286 0.59410714 0.59642857 0.59625    0.59660714
        nan 0.59625    0.59571429 0.59607143 0.59607143 0.59625
        nan 0.5944642

GridSearchCV(cv=5, estimator=RandomForestClassifier(),
             param_grid={'criterion': ['gini', 'entropy'],
                         'max_depth': range(1, 10),
                         'min_samples_leaf': range(1, 10),
                         'n_estimators': [0, 5, 10, 20, 50, 120]},
             verbose=3)

In [20]:
rf2_grid.best_params_

{'criterion': 'gini',
 'max_depth': 7,
 'min_samples_leaf': 7,
 'n_estimators': 20}

- x1 and x2 datasets are giving kind of similar accuracy

In [21]:
f1_score(y2_test, rf2_grid.predict(x2_test), average= 'macro')

0.4757370366569503

## Bag of random forest with x2 data

In [23]:
accuracy_rf =[0]
for i in range(1,20):
    bag_rf = BaggingClassifier(RandomForestClassifier(criterion='gini', max_depth=7, min_samples_leaf=7,
                                                     n_estimators = 20), n_estimators= i)
    bag_rf.fit(x2_train,y2_train)
    print(i,f1_score(y2_test, bag_rf.predict(x2_test), average= 'macro'))
    accuracy_rf.append(f1_score(y2_test, bag_rf.predict(x2_test), average= 'macro'))

C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


1 0.46462130151654213


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


2 0.44516108215333616


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


...

17 0.4669347223491426


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


18 0.46523654898763006


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


19 0.4501947881322046


In [24]:
max(accuracy_rf)

0.48104796924167526

In [25]:
# more steps

for i in range(20,50):
    bag_rf = BaggingClassifier(RandomForestClassifier(criterion='gini', max_depth=7, min_samples_leaf=7,
                                                     n_estimators = 20), n_estimators= i)
    bag_rf.fit(x2_train,y2_train)
    print(i,f1_score(y2_test, bag_rf.predict(x2_test), average= 'macro'))
    accuracy_rf.append(f1_score(y2_test, bag_rf.predict(x2_test), average= 'macro'))

C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


20 0.4770978110627346


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


21 0.4755336948027978


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


...

47 0.4691943127962085


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


48 0.47755171098744637


C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


49 0.47497723115543283


In [26]:
max(accuracy_rf)

0.4836625681411852

In [28]:
np.argmax(np.array(accuracy_rf))

45

In [30]:
accuracy_rf[45]   # accuracy 1% increase by bagging

0.4836625681411852

- both x1 and x2 dataset are playing same roll so we can go with x2 dataset since it has less column

## Bag of random forest main model

In [37]:
bag_rf = BaggingClassifier(RandomForestClassifier(criterion='gini', max_depth=7, min_samples_leaf=7,
                                                     n_estimators = 20), n_estimators= 45)

In [38]:
 bag_rf.fit(x2_train,y2_train)

C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


BaggingClassifier(base_estimator=RandomForestClassifier(max_depth=7,
                                                        min_samples_leaf=7,
                                                        n_estimators=20),
                  n_estimators=45)

In [39]:
f1_score(y2_test, bag_rf.predict(x2_test), average= 'macro')

0.47438433045312484

## Creating submission dataset

In [40]:
df_submission = pd.read_csv('test_4zJg83n.csv')

In [41]:
df_submission.head()

loan_id  age  education proof_submitted  loan_amount  asset_cost  \
0     7001   29        1.0          Aadhar       636936      768240   
1     7002   28        1.0          Aadhar       548988      693060   
2     7003   28        1.0          Aadhar       651756      936600   
3     7004   45        2.0          Aadhar       614676      744840   
4     7005   48        1.0          Aadhar       625236      839400   

   no_of_loans  no_of_curr_loans  last_delinq_none  
0            2                 2                 0  
1            3                 3                 0  
2            0                 0                 0  
3            4                 3                 0  
4            0                 0                 0

In [42]:
df_submission.isna().sum()

loan_id              0
age                  0
education           92
proof_submitted      0
loan_amount          0
asset_cost           0
no_of_loans          0
no_of_curr_loans     0
last_delinq_none     0
dtype: int64

In [44]:
df_submission.drop(['loan_id','education','proof_submitted','no_of_curr_loans'], axis = 1,inplace= True) # since our model build with x2 dataset

In [45]:
df_pred = bag_rf.predict(df_submission)

In [49]:
df_pred

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [53]:
loan_id = [(i) for i in range(7001,10001)]

In [54]:
submission_df = pd.DataFrame({'loan_id':loan_id,'loan_default': df_pred})

In [59]:
submission_df.to_csv('bag_random_forest_submission.csv', index=False)

## training with full dataset

In [64]:
def pred_to_submit_file(model, file_name):
    df_pred = model.predict(df_submission)
    loan_id = [(i) for i in range(7001,10001)]
    submission_df = pd.DataFrame({'loan_id':loan_id,'loan_default': df_pred})
    submission_df.to_csv(file_name, index=False)


In [63]:
bag_rf1 =  BaggingClassifier(RandomForestClassifier(criterion='gini', max_depth=7, min_samples_leaf=7,
                                                     n_estimators = 20), n_estimators= 45)
bag_rf1.fit(x2,y2)

C:\Users\Saikat\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


BaggingClassifier(base_estimator=RandomForestClassifier(max_depth=7,
                                                        min_samples_leaf=7,
                                                        n_estimators=20),
                  n_estimators=45)

In [66]:
pred_to_submit_file(bag_rf1,'bag_random_forest_full.csv' )

## Sclaing 2nd type dataset

In [117]:
## scaling
scaler = StandardScaler()
x2_scale = pd.DataFrame(scaler.fit_transform(x2), columns= x2.columns)

In [118]:
x2_train_scale, x2_test_scale, y2_train_scale, y2_test_scale = train_test_split(x2_scale, y2, test_size=0.20, random_state=0)

In [122]:
df_submission_scaled =pd.DataFrame(scaler.transform(df_submission),columns=df_submission.columns)

In [123]:
df_submission_scaled

age  loan_amount  asset_cost  no_of_loans  last_delinq_none
0    -0.935340    -0.176361   -0.690330    -0.155950         -0.116037
1    -1.067142    -0.763455   -1.040857     0.026814         -0.116037
2    -1.067142    -0.077430    0.094650    -0.521478         -0.116037
3     1.173487    -0.324957   -0.799432     0.209578         -0.116037
4     1.568892    -0.254464   -0.358546    -0.521478         -0.116037
...        ...          ...         ...          ...               ...
2995 -0.803538    -2.066374   -0.431952    -0.521478         -0.116037
2996 -0.539935     0.694308    0.014362     0.209578         -0.116037
2997  0.909883    -0.159538   -0.667726    -0.155950         -0.116037
2998 -0.539935     0.158561   -0.039966    -0.521478         -0.116037
2999  0.778082    -0.101462   -0.751315     0.392342         -0.116037

[3000 rows x 5 columns]

## With ANN

In [124]:
import tensorflow as tf
from tensorflow import keras

model = keras.Sequential([keras.layers.Dense(5, activation = 'relu'),
                          keras.layers.Dense(100, activation = 'relu'),
                         keras.layers.Dense(2, activation = 'sigmoid')])

model.compile(optimizer = 'adam',
             loss = 'sparse_categorical_crossentropy',
             metrics = ['SparseCategoricalAccuracy'])
model.fit(x2_train_scale, y2_train_scale, epochs = 40)

Epoch 1/40

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

175/175 [==============================] - 0s 884us/step - loss: 0.6742 - sparse_categorical_accuracy: 0.5943
Epoch 2/40
175/175 [==============================] - 0s 609us/step - loss: 0.6674 - sparse_categorical_accuracy: 0.5936
Epoch 3/40
175/175 [==============================] - 0s 587us/step - loss: 0.6651 - sparse_categorical_accuracy: 0.5955
Epoch 4/40
175/175 [==============================] - 0s 727us/step - loss: 0.6640 - sparse_categorical_accuracy: 0.5970
Epoch 5/40
175/175 [====

In [125]:
prob_pred = model.predict(x2_test_scale)

In [126]:
nn_pred = []
for i in range(len(prob_pred)):
    pred = np.argmax(prob_pred[i])
    nn_pred.append(pred)

In [128]:
nn_pred = np.array(nn_pred)

In [129]:
f1_score(y2_test_scale, nn_pred, average= 'macro')

0.5329472363820759

In [130]:
prob_pred = model.predict(df_submission_scaled)
nn_pred = []
for i in range(len(prob_pred)):
    pred = np.argmax(prob_pred[i])
    nn_pred.append(pred)
nn_pred = np.array(nn_pred)

In [131]:
loan_id = [(i) for i in range(7001,10001)]
submission_df = pd.DataFrame({'loan_id':loan_id,'loan_default': nn_pred})
submission_df.to_csv('neural_network2.csv', index=False)